## DeepDream with InceptionV3

<img src="http://science.slc.edu/jmarshall/bioai/images/dd1_small.jpg" width="55%">

The DeepDream algorithm is almost identical to the filter-visualization technique we explored for individual filters, in which we used gradient ascent to find an input image that maximizes the response of a particular filter within a layer.  But there are three key differences:

* DeepDream finds an image that maximizes the activation of an entire set of layers rather than a specific filter within a layer.
* Instead of starting with a noisy blank image, we start with an existing image.
* Input images are processed at different scales, called *octaves*.

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import tensorflow as tf

We'll load just the pretrained **InceptionV3** convolutional base, without the classification layers, so that we can feed images of any size into the network.

In [ ]:
from tensorflow.keras.applications import InceptionV3

iv3 = InceptionV3(weights="imagenet", include_top=False)

In [ ]:
iv3.summary()

### Load the Images

In [ ]:
def load_image_file(filename):
    url = "http://science.slc.edu/jmarshall/bioai/images/" + filename
    image_path = tf.keras.utils.get_file(filename, origin=url)
    jpeg_img = tf.keras.utils.load_img(image_path)
    return np.array(jpeg_img)

In [ ]:
elephants = load_image_file('elephants.jpg')
jellyfish = load_image_file('jellyfish.jpg')
flamingos = load_image_file('flamingos.jpg')
tiger = load_image_file('tiger.jpg')

In [ ]:
type(elephants)

In [ ]:
elephants.min(), elephants.max(), elephants.dtype, elephants.shape

In [ ]:
plt.imshow(elephants);

In [ ]:
from tensorflow.keras.applications.inception_v3 import preprocess_input

# converts an image of ints in the range [0, 255] to a batch tensor
# of shape (1, height, width, 3) of floats in the range [-1.0, 1.0]

def preprocess_image(image):
    return np.array([preprocess_input(image)])

In [ ]:
# converts a floating-point array into a displayable RGB image of integers in the range [0, 255]

def deprocess_image(batch):
    image = batch.reshape((batch.shape[1], batch.shape[2], 3))  # reshape as a single image
    new_image = image - image.mean()
    new_image /= new_image.std()
    new_image *= 64
    new_image += 128
    new_image = new_image.clip(0, 255).astype('uint8')
    return new_image

In [ ]:
img = elephants

In [ ]:
img.min(), img.max(), img.dtype, img.shape

In [ ]:
img2 = preprocess_image(img)

In [ ]:
img2.min(), img2.max(), img2.dtype, img2.shape

In [ ]:
img3 = deprocess_image(img2)

In [ ]:
img3.min(), img3.max(), img3.dtype, img3.shape

In [ ]:
plt.imshow(img3);

### Gradient Ascent in Image Space

This dictionary specifies which layers of the network will be used to construct the dream image, as well as their relative weightings:

In [ ]:
layer_contributions = {
    "mixed4": 1.0,
    "mixed5": 1.5,
    "mixed6": 2.0,
    "mixed7": 2.5,
}

In [ ]:
layer_features = dict([(name, iv3.get_layer(name).output) for name in layer_contributions])

In [ ]:
layer_features

In [ ]:
iv3.input

In [ ]:
from tensorflow.keras.models import Model

feature_extractor = Model(inputs=iv3.input, outputs=layer_features)

In [ ]:
feature_extractor(iv3.input)

This is the function to be optimized:

In [ ]:
def compute_response(batch, feature_extractor):  # batch contains a single image
    layer_features = feature_extractor(batch)
    response = tf.zeros(shape=())
    for layer_name, coeff in layer_contributions.items():
        features = layer_features[layer_name]
        response += coeff * tf.reduce_mean(tf.square(features[:,2:-2,2:-2,:]))  # remove border pixels
    return response

In [ ]:
compute_response(iv3.input, feature_extractor)

In [ ]:
@tf.function
def gradient_ascent_step(image, feature_extractor, step_size):
    with tf.GradientTape() as tape:
        tape.watch(image)
        response = compute_response(image, feature_extractor)
    gradient = tape.gradient(response, image)  # gradient = d_response/d_image
    gradient = tf.math.l2_normalize(gradient)
    image += step_size * gradient
    return response, image

In [ ]:
def gradient_ascent_loop(image, feature_extractor, iterations, step_size, max_response, quiet):
    for i in range(iterations):
        response, image = gradient_ascent_step(image, feature_extractor, step_size)
        if max_response is not None and response > max_response:
            if not quiet:
                print(f"... Exceeded max allowed response of {max_response}")
            break
        if not quiet:
            print(f"... Response value at step {i}: {response:.2f}")
    return image

### The DeepDream Algorithm

<img src="http://science.slc.edu/jmarshall/bioai/images/dd_algorithm.jpg" width="90%">

In [ ]:
def size_sequence(height, width, num_octaves=3, scale_factor=1.4):
    sizes = [(height, width)]
    for i in range(1, num_octaves):
        height, width = int(height/scale_factor), int(width/scale_factor)
        sizes.append((height, width))
    return sizes[::-1]  # reverses the list

In [ ]:
size_sequence(467, 699)

In [ ]:
size_sequence(350, 350)

In [ ]:
size_sequence(350, 350, num_octaves=5)

In [ ]:
size_sequence(350, 350, num_octaves=5, scale_factor=1.6)

In [ ]:
size_sequence(350, 350, num_octaves=5, scale_factor=2)

### Parameters
<pre>
cycles          <i>maximum number of cycles of gradient ascent</i>
step_size       <i>gradient ascent step size</i>
num_octaves     <i>number of dream/upscale cycles</i>
scale_factor    <i>upscale factor</i>
max_response    <i>stop gradient ascent if response exceeds this value</i>
quiet           <i>controls level of output</i>
</pre>

In [ ]:
# This version is not exactly equivalent to the book's code, but it is consistent with Figure 12.6
# in the book. In the book's version, the order of operations is: upscale, dream, reinject details,
# but here it is: dream, upscale, reinject details.

def deep_dream(image, cycles=30, step_size=20, num_octaves=3, scale_factor=1.4, max_response=15, quiet=False):
    # image can be a numpy image or a filename string
    if type(image) == np.ndarray and image.dtype == 'uint8':
        pass
    elif type(image) == str:
        image = load_image_file(image)
    else:
        print("image must be an int array in the range [0,255] or an image filename")
        return
    
    layer_features = dict([(name, iv3.get_layer(name).output) for name in layer_contributions])
    feature_extractor = Model(inputs=iv3.input, outputs=layer_features)
    
    height, width = image.shape[0], image.shape[1]
    sizes = size_sequence(height, width, num_octaves, scale_factor)
    print(f"Size sequence is", sizes)
    
    # original is a batch tensor of float32 values in the range [-1.0, 1.0]
    original = preprocess_image(image)
    scaled_originals = [tf.image.resize(original, size) for size in sizes]
    
    img = tf.identity(scaled_originals[0])  # makes a copy of the image
    for i in range(num_octaves):
        print(f"Processing image size {sizes[i]}")
        # dream
        img = gradient_ascent_loop(img, feature_extractor, cycles, step_size, max_response, quiet)
        
        if i != num_octaves-1:
            # upscale image
            img = tf.image.resize(img, sizes[i+1])
            # reinject lost details
            upscaled_original = tf.image.resize(scaled_originals[i], sizes[i+1])
            lost_detail = scaled_originals[i+1] - upscaled_original
            img += lost_detail
  
    dream = deprocess_image(img.numpy())

    plt.axis('off')
    plt.imshow(dream)
    plt.show()

    # To save the dream to a file, uncomment the lines below:
    #tf.keras.utils.save_img("dream.png", dream)
    #print('Image saved as dream.png')

In [ ]:
deep_dream(elephants)

In [ ]:
plt.imshow(jellyfish);

In [ ]:
layer_contributions = {
    "mixed4": 3.5,
    "mixed5": 3.0,
    "mixed6": 1.0,
    "mixed7": 5.0,
}

In [ ]:
deep_dream(jellyfish)

In [ ]:
plt.imshow(flamingos);

In [ ]:
layer_contributions = {
    "mixed4": 5.0,
    "mixed5": 4.0,
    "mixed6": 2.0,
    "mixed7": 1.0,
}

In [ ]:
deep_dream(flamingos, num_octaves=4)

In [ ]:
plt.imshow(tiger);

In [ ]:
deep_dream(tiger)

In [ ]:
deep_dream(tiger, cycles=50, num_octaves=4, scale_factor=1.5, max_response=500)